In [8]:
import os
from pathlib import Path
# Setting the working directory to the root of the project
project_dir = Path("C:/Users/adbou/source/repos/KFHXRelatedAi/")
os.chdir(project_dir)

from Configs.GeneralPaths import SOURCEDATA
import pandas as pd

In [9]:
#loading the csv into pandas df

unique_detailed_mcc_path = SOURCEDATA / "Unique_Detailed_MCC.xlsx"

unique_mccs = pd.read_excel(unique_detailed_mcc_path)

In [10]:
unique_mccs

MCC                                Detailed MCC
0   5812               Restaurants and Food Services
1   5732                  Electronics and Appliances
2   7230               Personal Services - Hair Care
3   4814       Technology and Communication Services
4   5262                        Digital Goods-Market
..   ...                                         ...
73  7393                           Security Services
74  5969                            Direct Marketing
75  5972  Specialty Stores - Stamp and Coin Supplies
76  7251        Footwear and Accessories Maintenance
77  5131      Specialty Stores - Fabrics and Notions

[78 rows x 2 columns]

In [11]:
from openai import OpenAI
client = OpenAI(api_key='sk-proj-lFCD6KXRS7R8kAaloineT3BlbkFJVlUaTzD3sIS4hzX9U0Fe')
EMBEDDING_MODEL = "text-embedding-3-large"

In [12]:
def get_Text_Embeddings(text):
    text = text.replace("\n", " ")
    print(f"Unique MCC embedding : {client.embeddings.create(input=[text],model=EMBEDDING_MODEL).data[0].embedding} " )
    return client.embeddings.create(input=[text],model=EMBEDDING_MODEL).data[0].embedding


unique_mccs['ada_embedding'] = unique_mccs["Detailed MCC"].apply(lambda x: get_Text_Embeddings(x))

Unique MCC embedding : [0.01598844863474369, 0.021374518051743507, -0.020710906013846397, 0.013411159627139568, 0.01071812491863966, -0.0256494227796793, 0.001219196361489594, -0.05114451423287392, -0.029291577637195587, -0.000584519759286195, 0.004815054126083851, -0.01359635405242443, -0.043242890387773514, 0.0047726137563586235, -0.007643126416951418, 0.017176778987050056, -0.000546419876627624, -0.03456961736083031, 0.005771891679614782, -0.003619006834924221, -0.00939861498773098, 0.022068997845053673, -0.014854133129119873, -0.012570069171488285, 0.038952551782131195, 0.020834367722272873, -0.01158236525952816, 0.007932492531836033, 0.03777965530753136, 0.012840144336223602, 0.009714988991618156, 0.01665206253528595, 0.03000148944556713, -0.03864389657974243, 0.018426841124892235, 0.015363417565822601, -0.0006756701623089612, 0.019985560327768326, 0.04012544825673103, 0.01723851077258587, -0.026976648718118668, -0.031020060181617737, -0.028828592970967293, 0.021050428971648216, -

In [13]:
unique_mcc_embeddings_df = unique_mccs[['MCC', 'ada_embedding']]


In [14]:
unique_mcc_embeddings_df

MCC                                      ada_embedding
0   5812  [0.01598844863474369, 0.021374518051743507, -0...
1   5732  [-0.044819995760917664, 0.02276458591222763, -...
2   7230  [0.009587069042026997, 0.0010589455487206578, ...
3   4814  [0.01326761394739151, 0.00438289949670434, -0....
4   5262  [-0.05530184507369995, -0.024139152839779854, ...
..   ...                                                ...
73  7393  [0.013662679120898247, 0.0035436409525573254, ...
74  5969  [0.009723884984850883, 0.0003069668891839683, ...
75  5972  [0.015417693182826042, 0.021184373646974564, -...
76  7251  [-0.03005962073802948, 0.0038998755626380444, ...
77  5131  [0.0012094506528228521, 0.025986818596720695, ...

[78 rows x 2 columns]

In [15]:
unique_mcc_embeddings_df.to_csv(Path(SOURCEDATA / "Unique_MCCs_Embeddings.csv") , index=False)

In [16]:
import ast

unique_mcc_embeddings_new = pd.read_csv(Path(SOURCEDATA / "Unique_MCCs_Embeddings.csv"))
unique_mcc_embeddings_new['ada_embedding'] = unique_mcc_embeddings_new['ada_embedding'].apply(ast.literal_eval)

unique_mcc_embeddings_new.head()

MCC                                      ada_embedding
0  5812  [0.01598844863474369, 0.021374518051743507, -0...
1  5732  [-0.044819995760917664, 0.02276458591222763, -...
2  7230  [0.009587069042026997, 0.0010589455487206578, ...
3  4814  [0.01326761394739151, 0.00438289949670434, -0....
4  5262  [-0.05530184507369995, -0.024139152839779854, ...

In [17]:
from sklearn.metrics.pairwise import cosine_similarity

def calculate_cosine_similarity(embedding, embeddings):
    similarities = cosine_similarity([embedding], embeddings)
    return similarities[0]

In [22]:
given_content_id = 3038


given_embedding = unique_mcc_embeddings_new[unique_mcc_embeddings_df['MCC'] == given_content_id]['ada_embedding'].values[0]
embeddings_list = unique_mcc_embeddings_new['ada_embedding'].tolist()
similarities = calculate_cosine_similarity(given_embedding, embeddings_list)

# Add similarities to the DataFrame
unique_mcc_embeddings_new['similarity'] = similarities
sorted_embeddings_df = unique_mcc_embeddings_new.sort_values(by='similarity', ascending=False)

In [24]:
top_5_similar = sorted_embeddings_df.head(10)
top_5_similar

MCC                                      ada_embedding  similarity
5   3038  [-0.01413386408239603, -0.009622327983379364, ...    1.000000
16  7523  [-0.01693022809922695, -0.006166267208755016, ...    0.690009
34  4468  [-0.016200199723243713, -0.013334488496184349,...    0.528890
48  4111  [-0.01470107864588499, 0.024178599938750267, -...    0.526483
57  5962  [-0.0006830694037489593, 0.007142612710595131,...    0.402831
29  7512  [-0.021089477464556694, 0.03430729731917381, -...    0.392698
17  3583  [0.00440142210572958, 0.03289124742150307, -0....    0.392384
18  9399  [-0.015760226175189018, 0.01850198023021221, -...    0.349481
11  5533  [0.009567225351929665, 0.027165334671735764, -...    0.345795
3   4814  [0.01326761394739151, 0.00438289949670434, -0....    0.337873